re.compile(r'[ .,?!가-힣ㅋㅎㅜㅠa-zA-Z0-9]+')

1. 띄어쓰기 해주기
2. 중복 글자 처리
3. 문장 나누기
4. 1단어 제거

1. data fommat 통일
2. 각 데이터 전처리 파이프라인 통과
3. 각 데이터 train, test 데이터셋 생성

In [1]:
import re
from pykospacing import spacing
from soynlp.normalizer import repeat_normalize
from kss import kss
import pandas as pd
from tqdm.notebook import tqdm
import numpy as np

In [11]:
# 데이터 포멧 통일 작업 #
# 추후 전처리 프로세스 통일을 위해 #
# 컬럼 2개(text, label) #

def data_format_setting_hotel(dataFileName):
    data = pd.read_csv(dataFileName)
    data.columns = ['text', 'label']
    data.drop_duplicates(subset=['text'], inplace=True)
    data = data.dropna(axis=0)
    data.to_csv('data/origin/hotel.txt', sep = '\t', index = False)
    
def data_format_setting_movie(dataFileName):
    data = pd.read_table(dataFileName)
    data = data.drop(['id'], axis=1)
    data.columns = ['text', 'label']
    data.drop_duplicates(subset=['text'], inplace=True)
    data = data.dropna(axis=0)
    data.to_csv('data/origin/movie.txt', sep = '\t', index = False)
    
def data_format_setting_shopping(dataFileName):
    data = pd.read_table(dataFileName, header=None)
    data.columns = ['rating', 'text']
    data['label'] = np.select([data.rating > 3], [1], default=0)
    data = data.drop(['rating'], axis=1)
    data.drop_duplicates(subset=['text'], inplace=True)
    data = data.dropna(axis=0)
    data.to_csv('data/origin/shopping.txt', sep = '\t', index = False)

data_format_setting_movie('data/origin/ratings_train.txt')
data_format_setting_hotel('data/origin/hotel_pos_neg.csv')
data_format_setting_shopping('data/origin/naver_shopping.txt')    

In [12]:
del_filter1 = re.compile(r'[!?,.ㅋㅎㅜㅠ가-힣0-9]+')
del_filter2 = re.compile(r'[ㅋㅎㅜㅠ가-힣0-9]+')

# label = 텍스트가 있는 컬럼 이름
def regex_spacing_normalization(data, label):
    for idx, item in tqdm(enumerate(data[label])):
        tmp = ' '.join(del_filter1.findall(item))
        tmp = spacing(tmp)
        tmp = repeat_normalize(tmp, num_repeats=2)
        data.at[idx, label] = tmp

# label = 텍스트가 있는 컬럼 이름
def regex_specialChar(data, label):
    for idx, item in tqdm(enumerate(data[label])):
        tmp = ' '.join(del_filter2.findall(item))
        data.at[idx, label] = tmp
        
def split_sentence(data):
    arr = []
    for sentence in data:
        for s in kss.split_sentences(sentence):
            arr.append(s)
    return arr

# TextCol = 리뷰 텍스트가 있는 컬럼 이름
# labelCol = 라벨링 되어있는 컬럼 이름
def neg_pos_split(data, TextCol, labelCol):
    neg = data[data[labelCol] == 0][TextCol]
    pos = data[data[labelCol] == 1][TextCol]

    neg = pd.DataFrame({TextCol: split_sentence(neg)})
    pos = pd.DataFrame({TextCol: split_sentence(pos)})

    neg[labelCol] = 0
    pos[labelCol] = 1

    # del record that have only 1 word
    review_splited = pd.concat([pos, neg])
    review_splited["len_text"] = [len(t.split()) for t in review_splited[TextCol]]
    review_splited_del_meaningless = review_splited[review_splited["len_text"] > 1]
    # flushing idx

    review_splited_del_meaningless.index = [i for i in range(review_splited_del_meaningless[TextCol].size)]
    review_splited_del_meaningless = review_splited_del_meaningless.drop(['len_text'], axis = 1)
    return review_splited_del_meaningless

def preprocessingPipeLine(data):
    regex_spacing_normalization(data, 'text')
    data = data.dropna(axis=0)
    pre_data = neg_pos_split(data, 'text', 'label')
    pre_data = pre_data.dropna(axis=0)
    regex_specialChar(pre_data, 'text')
    pre_data = pre_data.dropna(axis=0)
    pre_data.drop_duplicates(subset=['text'], inplace=True)
    return pre_data
hotelData = pd.read_table('data/origin/hotel.txt')   
movieData = pd.read_table('data/origin/movie.txt')    
shoppingData = pd.read_table('data/origin/shopping.txt')     

pre_movieData = preprocessingPipeLine(movieData) 
pre_shoppingData = preprocessingPipeLine(shoppingData)
pre_hotelData = preprocessingPipeLine(hotelData) 



0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

In [9]:
tt = pd.read_table('data/origin/movie.txt')  

In [10]:
tt[25520:]

text  label
25520                            샘 킴 반지좀빼고요리하지 양손어다반지 비위생      0
25521                                                 NaN      1
25522                          진짜재밋어요!!! 또개봉했으면 좋겠다! 또봐야지      1
25523   벌써 12년 이나 흘러버렸네.. 추억은 추억일때 아름다운 법.. 5년 이상 영화는 ...      0
25524            보기 전부터 스토리는 기대도 안했고, 선수라도 보는 재미를 원했건만...      0
...                                                   ...    ...
146178                                인간이 문제지.. 소는 뭔죄인가..      0
146179                                      평점이 너무 낮아서...      1
146180                    이게 뭐요? 한국인은 거들먹거리고 필리핀 혼혈은 착하다?      0
146181                        청춘 영화의 최고봉.방황과 우울했던 날들의 자화상      1
146182                           한국 영화 최초로 수간하는 내용이 담긴 영화      0

[120663 rows x 2 columns]

In [14]:
import sklearn
from sklearn import model_selection

def hotel_data_split(data):
    label = data["label"]
    hotel_train, hotel_test = sklearn.model_selection.train_test_split(data, test_size = 0.5, stratify=label)
    return hotel_train, hotel_test

def data_balancing_process(data, n):
    label0_df = data.query('label==0').sample(n=n//2, random_state=2000)
    label1_df = data.query('label==1').sample(n=n//2, random_state=2000)
    dataTrain = pd.concat([label0_df, label1_df], ignore_index=True)
    dataTrain = dataTrain.iloc[np.random.permutation(dataTrain.index)]
    return dataTrain

def data_concat2(hotelData, data, saveFileName):
    trainData = pd.concat([hotelData, data], ignore_index=True)
    trainData = trainData.iloc[np.random.permutation(trainData.index)]
    trainData.to_csv(saveFileName, sep = '\t', index = False)

def data_concat3(hotelData, data1, data2, saveFileName):
    trainData = pd.concat([hotelData, data1, data2], ignore_index=True)
    trainData = trainData.iloc[np.random.permutation(trainData.index)]
    trainData.to_csv(saveFileName, sep = '\t', index = False)

pre_hotel_train, pre_hotel_test = hotel_data_split(pre_hotelData)
n = len(pre_hotel_train)

pre_movieData = data_balancing_process(pre_movieData, n)
pre_shoppingData = data_balancing_process(pre_shoppingData, n)

pre_movieData.to_csv('data/preprocessing/movie.txt', sep = '\t', index = False)
pre_shoppingData.to_csv('data/preprocessing/shopping.txt', sep = '\t', index = False)
pre_hotel_train.to_csv('data/preprocessing/hotel_train.txt', sep = '\t', index = False)
pre_hotel_test.to_csv('data/preprocessing/hotel_test.txt', sep = '\t', index = False)

hotelData = pd.read_table('data/preprocessing/hotel_train.txt')   
movieData = pd.read_table('data/preprocessing/movie.txt')    
shoppingData = pd.read_table('data/preprocessing/shopping.txt')     


data_concat2(hotelData, movieData, 'data/sentiment_test_dataset/hotel_movie_train.txt')
data_concat2(hotelData, shoppingData, 'data/sentiment_test_dataset/hotel_shopping_train.txt')
data_concat3(hotelData, movieData, shoppingData, 'data/sentiment_test_dataset/hotel_movie_shopping_train.txt')

pre_hotel_train.to_csv('data/sentiment_test_dataset/hotel_train.txt', sep = '\t', index = False)
pre_hotel_test.to_csv('data/sentiment_test_dataset/hotel_test.txt', sep = '\t', index = False)

In [16]:
d1= pd.read_table('data/sentiment_test_dataset/hotel_shopping_train.txt')   
d1

text  label
0       거실이 다른 숙소에 비해 넓은 편이라 강아지와 함께 지 내기 좋았어요      1
1                          직원들끼리 소통이 전혀 없나 봅니다      0
2         머리 둘레 59여서 사이즈 샀더니 딱 맞는 느낌으로 들어 맞습니다      1
3                      새로 보내주신 이 제품마다 켜 지질 않네요      0
4                        매우 청결하고 인테리어도 너무 예뻤어요      1
...                                        ...    ...
103560                             이불이 너무 무거웠다      0
103561          쌀씻을 용도로 샀는데 구멍 너무 커서 쌀 다 빠져나가요      0
103562                   체크인 응대는 좀 더 친절했으면 합니다      0
103563           호텔 생각보다 시설이나 환경면에서는 많이 아쉬웠습니다      0
103564                                  싸게 샀네요      1

[103565 rows x 2 columns]

In [110]:

def data_concat_hotel_movie_train(naverTrainData, hotelTrainData):
    nTrain = pd.read_table(naverTrainData)
    hTrain = pd.read_csv("0.5hotel_train.csv")
    
    movie0_df = aa.query('label==0').sample(n=26255, random_state=2000)
    movie1_df = aa.query('label==1').sample(n=26255, random_state=2000)
    
    movieTrain = pd.concat([movie0_df, movie1_df], ignore_index=True)
    
    hTrain = hTrain.drop(['len_text'], axis=1)
    hTrain['id'] = 1
    hTrain = hTrain[['id', 'Text', 'Label']]
    hTrain.columns = ['id','document','label']
    #hTrain = hTrain.iloc[np.random.permutation(hTrain.index)].reset_index(drop=True)
    
    trainData = pd.concat([movieTrain, hTrain], ignore_index=True)
    trainData = trainData.iloc[np.random.permutation(trainData.index)]
    trainData.to_csv('sampleTrain.txt', sep = '\t', index = False)

def data_concat_hotel_movie_train(naverTrainData, hotelTrainData):
    nTrain = pd.read_table(naverTrainData)
    hTrain = pd.read_csv(hotelTrainData)
    
    movie0_df = aa.query('label==0').sample(n=26255, random_state=2000)
    movie1_df = aa.query('label==1').sample(n=26255, random_state=2000)
    
    movieTrain = pd.concat([movie0_df, movie1_df], ignore_index=True)
    
    hTrain = hTrain.drop(['len_text'], axis=1)
    hTrain['id'] = 1
    hTrain = hTrain[['id', 'Text', 'Label']]
    hTrain.columns = ['id','document','label']
    #hTrain = hTrain.iloc[np.random.permutation(hTrain.index)].reset_index(drop=True)
    
    trainData = pd.concat([movieTrain, hTrain], ignore_index=True)
    trainData = trainData.iloc[np.random.permutation(trainData.index)]
    trainData.to_csv('sampleTrain.txt', sep = '\t', index = False)
    
def data_concat_hotel_movie_train(naverTrainData, hotelTrainData):
    nTrain = pd.read_table(naverTrainData)
    hTrain = pd.read_csv(hotelTrainData)
    
    movie0_df = aa.query('label==0').sample(n=26255, random_state=2000)
    movie1_df = aa.query('label==1').sample(n=26255, random_state=2000)
    
    movieTrain = pd.concat([movie0_df, movie1_df], ignore_index=True)
    
    hTrain = hTrain.drop(['len_text'], axis=1)
    hTrain['id'] = 1
    hTrain = hTrain[['id', 'Text', 'Label']]
    hTrain.columns = ['id','document','label']
    #hTrain = hTrain.iloc[np.random.permutation(hTrain.index)].reset_index(drop=True)
    
    trainData = pd.concat([movieTrain, hTrain], ignore_index=True)
    trainData = trainData.iloc[np.random.permutation(trainData.index)]
    trainData.to_csv('sampleTrain.txt', sep = '\t', index = False)

AttributeError: 'NoneType' object has no attribute 'end'

In [67]:
pre_data.head(50)

Text  Label
0                                  직원 분들이 정말로 친절하십니다.      1
1   외국인 친구를 데리고 갔는데 특히 아침 조식 때 직원분이 많이 도와주셔서 정말로 간...      1
2     그리고 데스크에 계신 직원분들도 체크 아웃하고 짐도 맡겨주시고 정말로 친절하셨습니다.      1
3                              방은 깨끗하고 특히 화장실이 청결했어요.      1
4                약간 작은 방이긴 하지만 위치도 명동역에서 분 거리라 좋았습니다.      1
5                                       침대 매트리스는 좋았어요      1
6                                           아침식사도 좋구요      1
7                                            편의시설 가까움      1
8                                              위치가 좋다      1
9                                     화장실이 넓고 위치가 좋아요      1
10                                        지하철에서 가깝습니다      1
11                                      화장실 편리하고 좋았어요      1
12                                    소음,기타시설은 마음에 듬.      1
13  화장실이 샤워실과 분리되어서 좋았고..베드가 두개라 좁아서 답답함만 빼면 깨끗하고 ...      1
14     지하철 역 과 가까웠고, 주변이 번화가였으나 씨끄럽지 않았고, 욕조가 있어서 좋았다      1
15                                  옆방 소음이 커서 잠을 못이뤘음      1
16                                        위치가 너무 좋아요!      1
17                                지하철역과도 가깝고 교통이 편리해요      1
18  가장좋은 점은 역시 주차문제를 해결할수 있다는거와 강남역 앞이라서 놀거리 먹거리 풍...      1
19         침대도 편하고 불도 잘 들어왔고 바로 옆에 유명한 빵집이 있어서 좋았습니다.      1
20                                       강남역 접근성은 좋음.      1
21                              위치는 좋았음 그거 말고는 잘 모르겠음      1
22                                   위치와 친절 함, 쇼핑몰 근처      1
23                                    방 바닥? 이 엄청 따뜻해요      1
24                                      그리고 직원분 칠절합니다      1
25  조식이 잘 나옴 호선 몽촌토성역에서 찾아갈 것 생각하면 위치 나쁘지 않음 먹자골목에...      1
26                   위치도 좋고, 주위에 편의점 등 시설이용이 쉬워서 좋았음.      1
27  비싸기만한 조식뷔페보다 좋았던 조식의 구성, 쾌적한 룸. 티비에 넷플릭스랑 유튜브 ...      1
28  거의 일 동안 잠만 잤기에 크게 불편한점은 없었음. 호텔과 모텔 딱 그 중간 수준 ...      1
29  솔직히 잠만 자면 되었기에 룸 컨디션을 따지지 않았는데 가격대비 손해보는거 없이 적...      1
30  쿠션같은거에 뭔가 찝찝한 흔적이 있었지만 침구 그 자체는 흰색으로 깔끔하게 유지 되...      1
31                  일 잤지만 침구가 변함없이 정말 청결해서 기분이 좋았습니다.      1
32                    저는 그 부분에 깐깐한편이데 침구가 깔끔해서 만족입니다.      1
33  또한 발렛서비스가 되고 출차할때도 기분 좋게 나갈수 있도록 누르니 잘 준비해주셔서 ...      1
34  직원들이 친절했고 가격에 비해 위치나 청결이 괜찮았음 넷플릭스가 나오고 근처에 석촌...      1
35                             직원분들 친절하고, 스파욕조도 좋았어요.      1
36                                     거격대비 아주 좋았습니다.      1
37                             다른사람에게도 꼭 추천 해주고 싶더라구요      1
38                                덕분에 편한한 잠자리가 되었습니다.      1
39                                      식사구성이 굉장히 좋네요      1
40  맛집 거리 안에 위치한 숙소들 중에 외관부터 다른 숙소보다 신경쓴 것이 느껴지고 내...      1
41                  유튜브 보며 놀기도 좋고 노래방 하루 곡도 알짜 재미였어요.      1
42               롯데월드나 아쿠아리움 가는 길에 석촌호수 지나갈 수 있어 좋아요.      1
43                생각 외로 가성비가 좋았고 조식도 예쁘게 플레이팅 되어 나왔어요      1
44                                방음만 괜찮다면 재방문 의사 있어용      1
45                     병원땜에 묵었는데 편안하고 생각보다 깔끔 하긴했습니다.      1
46                  병원가기 좋은 위치인 듯 특히 아산병원 천호 미즈여성병원등등      1
47                        위치가 좋고 아침에 정성가득한 조식이 좋았습니다.      1
48                             무료셔틀과 웰컴 드링크 서비스가 좋았어요      1
49                        직원들 모두 친절하게 응대해주셔서 너무 좋았습니다      1

In [19]:
for item in data['Text']:
    item =

직원 분들이 정말로 친절하십니다. 외국인 친구를 데리고 갔는데 특히 아침 조식 때 직원분이 많이 도와주셔서 정말로 간사했습니다. 그리고 데스크에 계신 직원분들도 체크 아웃하고 짐도 맡겨주시고 정말로 친절하셨습니다. 방은 깨끗하고 특히 화장실이 청결했어요. 약간 작은 방이긴 하지만 위치도 명동역에서 2분 거리라 좋았습니다.
침대 매트리스는 좋았어요 아침식사도 좋구요
편의시설 가까움
위치가 좋다
화장실이 넓고 위치가 좋아요
지하철에서 가깝습니다 2분정도
화장실 편리하고 좋았어요
위치가좋음
소음,기타시설은 마음에 듬.
화장실이 샤워실과 분리되어서 좋았고..베드가 두개라 좁아서 답답함만 빼면 깨끗하고 좋았어요
지하철 역 과 가까웠고, 주변이 번화가였으나 씨끄럽지 않았고, 욕조가 있어서 좋았다
옆방 소음이 커서 잠을 못이뤘음
위치가 너무 좋아요! 지하철역과도 가깝고 교통이 편리해요
없음
강남역인근이라위치좋았음
가장좋은 점은 역시 주차문제를 해결할수 있다는거와 강남역 앞이라서 놀거리 먹거리 풍부한 지역에 위치해 지리적으로 완벽했습니다
침대도 편하고 불도 잘 들어왔고 바로 옆에 유명한 빵집이 있어서 좋았습니다.
강남역 접근성은 좋음.
위치는 좋았음
그거 말고는 잘 모르겠음
위치와 친절 함, 쇼핑몰 근처
방 바닥? 이 엄청 따뜻해요
그리고 직원분 칠절합니다 ^^
조식이 잘 나옴 8호선 몽촌토성역에서 찾아갈 것 생각하면 위치 나쁘지 않음 먹자골목에 있어서 식사 문제는 없지만 생각보다 외진 골목에 있음
위치도 좋고, 주위에 편의점 등 시설이용이 쉬워서 좋았음.
비싸기만한 조식뷔페보다 좋았던 조식의 구성,
쾌적한 룸. 티비에 넷플릭스랑 유튜브 있어서 실컷 봤어요.
거의 4~5일 동안 잠만 잤기에 크게 불편한점은 없었음. 호텔과 모텔 딱 그 중간 수준 느낌의 숙소였습니다. 솔직히 잠만 자면 되었기에 룸 컨디션을 따지지 않았는데 가격대비 손해보는거 없이 적정합니다. 쿠션같은거에 뭔가 찝찝한 흔적이 있었지만 침구 그 자체는 흰색으로 깔끔하게 유지 되어 있고 금방 햇빛에 건조시킨듯 청결

가격이 싼 편이고 위치가 적절함
위치가 좋았어요. 다른 호텔 같은 경우는 창이 없고 불투명해서 창문을 열어야 밖이 보이는데, 강남프리미어는 창이 투명해서 밖이 다 보여서 좋더라구요. 아침에 햇살을 볼 수 있어서 좋았습니다.
접근성이 대단히 좋았으며 첫 배정받고 난 방에서의 냄새로 인해 프론트로 요청하니 룸체인지가 수월했고 직원들의 친절함으로 아쉬움이 다소 덜했으며 룸이 생각보다 넓직하고 전체적으로 모던하고 편안했다.
브라이덜샤워파티하기에도 넓고 테이블이 많아서 좋았어요
강남/신논현에 있어서 위치적으로 좋았습니다.
이불이 편해서 좋았어요.
가격대비 나쁘지는 않음. 그냥 조식 제공하는 모텔느낌. 
직원들은 그냥 평범한 서비스 제공 했음.
8월3일 너무 더운날씨에 밖에 있다가 호텔 안으로 들어가니 그것만으로도 천국에 온 것 같았어요.
주변에 먹을곳과 마실곳이 많아 좋았어요.
위치가 좋음
별로임
위치 정말 좋았다. 신논현역에서 2분거리
숙소 사진을 너무 잘 찍어 홍보 하셨어요
신논현역 등 교통요지라 접근성이 좋을 뿐만아니라 24시 맛집이 있어 좋았음. 바로 앞 나주곰탕, 상무초밥, 설렁탕 추천합니다. 살짝 아쉽긴 하지만 호텔 지하 식당 조식과 점심도 먹을만 합니다.
지하철과 가깝고 논현동 먹자골목과도 가까워서
식사나 한 잔 한 후 호텔에 오기가 좋았음
조식이 저렴한데 맛이 괜찮음. 위치가 좋음. 아늑한 룸 컨디션 좋았습니다.
잠자리편안했어요~~~
.... 별로요. 짐도 안올려주시고 핸드폰충전기 두고나왔다니깐 전화해준다하고 전회 안해주더라고요 그리고 일단 직원들 표정이 다 별롭니다.
강남 신논현 위치네용
제공해주는 식사 및 음료들 전부 매우 만족스러웠습니다.
지불한 가격에 응당 맞는 대접이었으며, 어찌 보면 최고였습니다.
깔끔하고 위치가 좋았어요
직원분들도 친절했습니다!
1. 예쁜 스위트룸
2. 나름 친절
3. 피드백 빠른편
4. 예쁘고 깔끔한 편인 욕실
식사맛있어요 편안히 잘쉬었습니다
객실 깔끔하고 군더더기 없었습니다
위치가 최고
숙소의 위치가 지하철 및 버스 등 가

위치랑 청결이 많이 좋았어요!
마사지 최고~
여러곳 다녀지만. 10%할인받고 친절하고
너무 시원함
위치 좋음 가격 저렴함 딱 비즈니스호텔
기본옵셥들이 배치되어있어서 편리하게 사용할수있어서 좋았어요
다 좋았습니다.
가성비 역과의위치 스탭의 친절함 그외 기타 여러가지
리뷰 이벤트 레이트 체크아웃서비스 좋았습니다
데스크 직원이 나긋나긋 상냥 친절 그 자체였어요! 장소가 너무 좋아요! 대부분 관광지와 근접한 위치여서 좋았어요!!!
침대가..깨끗하고.좋음
주변 관광지와 가깝고 좋아요!
편안함. 접근성이 좋음.
예정보다 일찍 도착했는데도
친절하게 체크인을 도와줘서 편한 여행의 시작이 될수 있었습니다.
을지로3가역 1번출구 바로 앞에 위치 해 있어서, 접근성이 정말 좋았습니다.
청결도 서비스적인 부분에 대해서 불만은 전혀 없습니다.
외국인 관광객들이 많이 투숙하는 것으로 봐서 가성비 좋은 호텔이라고 생각합니다.
조식 마감이 너무 이르고, 20여 분이 남았는데도 먹을 수 있는 음식이 없어 황당했습니다.
직원분들이 친절하세요!
교통환경은 좋았어요
위치가 아주 좋았으며, 직원분들이 친절하였으며, 시설이 깨끗하고 잘 갖추어져 있어서 아주 안락하게 지냈습니다. 특히 주위에 맛있는 음식점들 빌리지가 형성되어 있어서 너무 좋았습니다. 호텔의 아침식사도 아주 좋았으며 풍족하였습니다. 다음에 다시 머물고 싶은 곳 이었습니다.
역 인근에 위치해있어 접근도 편했고 방도 깔끔했습니다.
덕분에 하루 푹쉬다 갑니다.
코로나시대에 가족과함께 단독룸에서 수영장은 너무 좋아요.
직원이친절하다
위치가 좋고 방과 욕실이 넓어요
카페트 바닥이 아닌 따뜻한 온돌 바닥이라 먼지도 적고 좋았어요
차를 가지고 갔는데 체크아웃후 출차에 어려움이 있었지만 직원분이 큰 도움을 주셔서 마지막까지 좋은 서비스를 받은 느낌
위치가 정말좋았어요
가격대비 위치나 시설은 좋아요 다만 호텔기본적인 어메니티가 없는거 빼고는
편안한 침구류, 넓은 욕조와 분리형 화장실이 가장 마음에 들었습니다.
대형차는 주차가 힘든점이 가장 아쉽습니다.

외관이 이쁨. 로비가 이쁨. 룸이 여자들 딱 좋아할 스타일.
예약할 때 요구사항을 들어주셨어요. 욕조가 깨끗해서 입욕 편안히 하고 왔네요^^ 침대 매우 푹신해서 좋았고 가운도 편했어요.
방 디자인이 예뻐요
조용했어요
객실 와이파이가되지않아 곤란했는데 바로 다른방으로 옮겨주시고 친절하게 문제해결해 주셨어요! 룸 컨디션은 매우 청결하고 깔끔합니다! 사진 그대로에요ㅎㅎ
가성비가 아주 뛰어난 호텔입니다.
건대입구역에서 걸어서 10분-15분 정도 거리에 위치하고 있습니다.
정확히는 화양시장?과 매우 가깝습니다.
야식을 화양시장에서 사와서 먹어도 좋습니다.
또한 근처에 예쁜 카페들이 많고, 둘러볼만한 번화가가 가까이 있습니다.
그랜드 부다페스트 영화의 호텔 이미지를 따라하려고 노력했던 호텔로 기억하고 있습니다.
로비와 지하의 BAR가 인테리어가 괜찮았습니다.
룸 콘디션은 깔끔한 편입니다. 다만, 왜 이렇게 쓸데 없이 화장실이 큰 건지... 너무 커서 띠용합니다.
방 따듯합니다.
피트니스 센터도 무료입니다. 넓지는 않지만 그래도 이정도 가격에 피트니스 센터가 있다는 점이 매우 만족스럽습니다.
아마 상주하는 직원(PT직원으로 추정)이 있는 것으로 기억합니다.
헬스복이나 운동복 양말은 당연히 개인지참입니다.
재방문 의사 있습니다.
지리적으로는 괜찮았고 직원분들도 친절했으며,추운날씨덕에 보일러를 너무 빵빵하게 해주셔서 되려 너무 더웠어요,
방이 작아서 좀 답답했지만 조용하고 안락했어요
여성취향 인테리어
이쁘게 꾸며놓은건 좋았네요~!
루프탑!!!
침구깨끗 매트리스 재질 걍 미쳣음
인테리어가 돋보인다
방음굿
위치와 청결도 정말 만족스러웠습니다.
컬러풀한 인테리어가 인상적이었습니다.
없어요
분위기가 좋았어요.
친구들이랑 갔는데 수영장도 놀기에 딱 적당해서 좋았고, 숙소 인테리어가 무엇보다 너무 깔끔하고 예뻤어요!! 저희 시끄럽게 놀았는데 방음도 잘되는 것 같았구요!! 덕분에 가격대비 진짜 잘 놀고올 수 있었습니다.
조식은 따로 하지 않았지만, 전반적인 숙소 분위기가 마음에 들었습니다

건강검진때문에 자주이용하는 호텔입니다 아파트형이라 우리가족 모두 편하게 잘쉬고 검진할수있었네요
도심에있어서좋았어요 
근처에. 덕수궁돌담길 산책도 좋았고.
투베드룸 아파트먼트를 이용하였는데, 공간이 정말 널찍해서 친구들과 파티를 즐기기에 츙분했어요. 쇼파와 테이블, 식탁과 주방이 갖춰져 있어 어떤 형태의 파티든 가능할것 같아요. 베드가 편안하고 베딩도 훌륭했습니다. 친구들과 다음파티도 여기서 하기로 했습니다.
위치가 좋고 내부 조리 시설이 있어서 좋았습니다.
위치, 서비스,매너, 가격대비 정말 훌륭하고 반려동물과 함께하기 너무 주변을 좋았어요
위치를, 매너굿, 가격대비 좋은위치에 크기도 좋고 조용한 곳으로 요청드렸는데 조용해서 숙면했어요 
가습기 요청에도 가져다주시고 반려동물로 짐이많은데 문도잡아주시도 매너가 좋은 호텔이라 기분좋게 있다 왔어요
거실 매우넓고 화장실 2개라 4명이서 지내기에 여유로웠습니다 침대 매우푹신합니다 가격대비 매우좋습니다
깨끗하고 편안했습니다
체크인 시간 지연되지 않고 직원분들이 친절함
레이트 체크아웃 가능한지 단순문의 했는데 한시간 무료 레이트 체크아웃 제공받음
숙소가 매우 넓고, 침구만 제외하면 쾌적하며 시설도 좋은 편에 속함
호텔에서 1km 이내 이화여고.가로수길 과 호텔로이어지는 돌담길도
아침.저녁 산책길로 추천합니다. 반려견 동반하여 숙박했는데 전혀 불편감
없이 너무 잘지내고 왔습니다.
위치, 가격가성비, 청결 만족스러웠습니다.
서울역 시청 모두 가까워요
처음 로비 딱 들어가는데 호텔냄새가너무 좋았어요ㅠㅠㅠ 힐링 ㅠㅠ수영모가없어서 메인풀에는 못들어갔지만 수영장 온수풀에서도 놀고, 침구도편안해서 호캉스 잘하구왔습니다! 관리가 되게 잘되고있는것같앗어용
레지던스라서 취사가 가능한 점이 좋았고 시설도 깔끔해서 좋아요 제가 실수로 컵을 깼는데 잘 해결해주셔서 감사드려요 ㅠㅜ 기회가 된다면 또 방문하겠습니다💕💕
세탁기랑 건조기 있는것!
친절한 직원분들과 좋은 위치
좋았구먼유
요리 해 먹기 좋음
시티에 있는데도 객실 넓음
가족 객실로 했었는데

...

전체적으로 소독 및 방역을 실시중이었으며 체크인 시에 리셉션에서 발열 체크를 해주셔서 청결 및 위생 관리에 상당히 신경 쓰고 있음이 느껴졌습니다. 내부 곳곳에 소독제가 비치되어 있었으며 청결한 방을 요청 드렸는데 아예 룸 업그레이드를 해주셔서 편안하게 잘 지내고 왔습니다. 위치도 역과 가까웠고 근방에 편의점이 있어서 이용이 용이했습니다.
방이 넓고 깨끗했어요 나중에 다시 오고싶습니다
편안하고 깨끗해서 출장시 이용하기 좋네요
늘 편안하게 이용하네요..
종종 이용하는데 편안하고 좋아요
위치, 청결은 엄청 좋았어요! 직원분들도 친절하시구요.
위치나 전반적인 청결도는 좋았습니다.
위치랑 시설이랑 모두 맘에 들었습니다!
다만 중국인관광객이 많아서 무서웟어여...
시내 중심에 있어 남대문, 명동, 서울역, 시청 등 걸어서 더니기 편해요
강력추천~~~~
침대 크고 편안하고, 청결하고, 친절하고 모두 좋았습니다. 2층 레스토랑도 맛있습니다.
서울 갈때 숙박하는 곳이예요~
대부분 가족이랑 이용하는데 언제가도 정말 편하게 이용합니다.
호텔에 트리플룸 잘 없는데 트리플 룸에서 3명이서 편하게 자고
난방도 잘되고~ 소파도 넓고 편해서 어무 좋았어요.
방이 엘리베이터 가까운 곳에 있었지만 소음도 없고
조용히 편하게 잘 쉬었습니다. 
다음에 또 이용할 의사 100프로에요 ㅋㅋㅋ
위치도 도보로 이동하기 좋고ㅡ정류장과 가까움.
깨끗하고 넓음.
침대가 푹신하고 물도 잘 나오고 조용해서 좋았어요.
객실이 넓고 깨끗해서 좋았어요~ 체크아웃 시간도 넉넉했고 직원분들도 친절했습니다
그 외는 다 매우좋았어요
가성비로는 최고
위치, 시설, 호텔 부대시설 모두 좋았습니다.
깨끗하고 따뜻하고 시청과 거리도 가깝고 좋았어요
직원분들이 아주 친절하셨어요^^
가족4명 머물기 거실공간 넓고 화장실 욕조 샤워부스 변기가 각각 문이 따로여서 너무 편안하고 좋았어요 덕수궁 걸어서 가깝고 주변 맛집도 모두 만족입니다
정말 모든게 마음에 들었어요
깨끗함, 방이 넓고 밤에 따뜻함, 침구가 좋음, 화장실이 좋음, 레스토랑이

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




옆방에서 크게 내는 소리가 들림
주변 편의시설이 많지 않았어요.
1. 처음 배정받은 방 화장실에 하수구냄새가 심하여 프론트에 문의하니 방을 곧바로 교체해주었다
2. 체크인시 조식이 코로나19 이슈로 뷔페가 아닌 서빙으로 제공된다고 했는데 예약과정에서 해당정보를 알 수 없었다
지난번 숙박할 때도 아쉬웠는데 주차장이 협소하고 따로 주차비를 받는건 좀 불편합니다.
난방을 틀면 시끄럽다는 점. 소리가 웅웅 크게 남. 비데가 혼자 작동해 밤에 자다 놀람
처리할 업무가 있어서 장시간 책상과 의자를 이용했는데 의자 불편함. 특히 히노키 욕조 사용 후 24시간이 지나도 욕조 바닥이 축축함. 샤워부스에 깔린 목재발판에서 곰팡이 냄새가 약간 나고 욕조 구석과 목재발판 끝에 검게 변색되고 떨어지는 부분도 보임.
Late checkout 이었는데 프론트에서 막 전화하고 그러셔서 좀 그랬어요
주차요금이 만원 추가로 발생하고, 예약 시 안내가 잘 이루어지지 않음.
방음이 전혀 안되서, 밖이나, 옆방 소리가 그대로 들림.
화장실과 방이 유리로 되어있어서 샤워나, 소변, 대변 볼 때 다 보이고, 블라인드가 있으나, 실루엣이 너무 뚜렷하게 보임.
거울이 화장실에만 있어요ㅠㅠ. 욕조는 조금 작습니다.
벽이 얇아서 방음이 전혀 안됩니다.
옆방 대화며 발소리가 다 들립니다..
욕조에 물이 넘치면 방안까지 흘러갑니다,,, 턱이 높낮이가 같아요
볼풀장 밑에 쿠션? 같은 것을 깔았다면 볼풀장 이용시 아동이 혹 다칠까 걱정안해도 될 거 같아요
난장시설이 좀 안 좋음. 우풍이 심해서 실내 온도 차이가 큼
잘때 추웠음
일일 주차비 있음, 냉장고 악취로 변경, 손이 안가는 구석에 청소 상태 불량
화장실문과 복도문이 같은 문이라 이용하기 불편했습니다.
창문이 열리지 않아 답답했습니다.
뷰가 좋은 편이라고 할 수 없었고 (위치상 어쩔 수 없어 보이긴 하지만)
실내 바닥과 화장실의 청소 상태가 아주 깨끗한 편이라고 볼 수는 없었다.
창문과 뷰를 볼수 없는 시설이여서 아쉬웠다.
커튼이없어서
밤인데도 방이너무 환해

역에서 너무 멀어요.
딱히 없었습니다.
화장실 구조가 특이하긴 한데.. 세면대와 샤워실 화장실이 다 따로따로 
세면대가 밖으로 나와있는 구조라 생각보다 불편했어요
물도 튀고, 샤워하러 들어갈때 옷을 걸어두기가 애매함....
참, 리버뷰라고 해서 기대하지 마세요 ㅎㅎㅎㅎㅎ
조식...
단체 이용이 많아 엘리베이터를 한참 기다려야 했습니다.
굳이 꼽자면 소파 쿠션..
싱글침대 폭이 너무 좁아서 자다가 떨어질 뻔 ㅠ
샤워기 수압이 약해요
딱히 없지만, 오후 피크시간대에는 수영장이 꽉 차서
이용하지 못한점이 아쉬웠습니다.
칫솔과 같은 일회용품 제공이 되지 않아요.
샤워부스 안 밖 옷 놓아둘 곳이 애매했어요
객실이 조금 좁은 편이며 화장실이 너무 붙어있어 조금 습하게 느껴졌습니다.
없습니다
다른싸이트보다 살짝 비쌌네요 네이버페이 언제주시죠?그거라도받으니 위안되네요
뷰가 공사판
욕실에 욕조가없는점
화장실문이유리라불편
룸서비스는 그저 그랬음. 맥주도 미지근한 상태로 줌. 미니바에 기본적으로 비치된 치약 칫솔도 없었음. 냉장고 성능이 매우 안좋음. 바디 스펀지도 없었음
욕실이 작아요
없어용
객실 세면대 쪽 콘센트는 정비를 해야할 것 같아요. 위험해 보였습니다
체크인할때 직원의 안내속도와 말이 잘 들리지않고 너무 빨릿어요
뷰가 생각보다 아쉬워요
샤워실 배수가 아쉽네요
엘리베이터가 너무 복잡했어요
화장실 구조가 익숙치 않았습니다.
수영장이 작아서 힘들겠지만 적어도 수영만 즐길 수 있는 레일을 한 레일 정도는 만들면 좋을 것 같습니다. 주로 어린친구들이 물장구 치고 놀고 있었는데 원래 매일 수영을 다니는 사람들은 출장중이나 여행중에도 수영을 즐기고 싶어서 수영장이 있는 호텔을 잡는 것일텐데 단순히 물놀이 용이어서 아쉬웠습니다. 또 드래곤시티는 4가지 호텔이 있어서 굉장히 헷갈리고 찾아보기 어려운 편인데 사이트에서 방의 옵션과 내부 사진이 많이 없어서 외부 블로그를 이용해 나에게 맞는 방을 찾아야 해서 아쉬웠습니다. 그마저도 결국 헷갈려서 세탁기가 있는 방이 필요했는데 없는 방을 예

5성 맞음?? 어떻게??
없음
에어컨이 약해요
수영장이 본관하고 떨어져있어 비오면 불편해요
없어요 좋았어요
야외수영장 운영한다더니 안하더라구요
딱히 없었던 거 같습니다.
자체내 마트나 간단한 쇼핑장소의 부족
공항근처의 소음이 조금 아쉬운점이었으나 이것을 뛰어넘는 동서양을 아우르는 훌륭한 조경과 경관시설때문에 큰 문제는 되지않았습니다. 
방음이 잘 되어 시끄럽지않습니다.
어메니티의 퀄리티는 좋습니다만 치약정도는 있었으면 합니다. 헬스장사용을 위해 운동화나 운동복 대여도 고려해주세요. 들고 다니기 곤란한 비지니스목적일 경우에 이용하는 호텔인것 같습니다.
그리고 사우나, 조식가격이 너무 비쌉니다.
편의점 등 주변 시설
비교적 오래된시설 
충전할 소켓이 불편 했음.
비행기 이륙하는 길이라 소음도
셔틀 기사랑 컨시어지의 콜 응대 직원이 무례해요
It smells bad at the bed near the toilet in my room
침대시트에 머리카락이 많았음
바닥에 먼지 많았음
예약확인 시 직원응대 아쉬움
새벽 화재 알람 비정상 작동시 직원의 안내 부족 및 직원들의 기본 태도가 부족해보임.
없음
방은 조금 연식이 있는 느낌
산책로에 대한 안내책자나
아이와 즐길 수 있는 것에 대한 설명이 적었어요.
간단히 즐길 음식도 많지 않았어요.
체크인&아웃이 flexible하지 않아 아쉬웠습니다
작은호텔도 아닌데‥
호텔수영장이수건을락커룸에비치하지않고키나눠줄때한사람에하나씩주는것으로바뀌었는데이건좀불편하네요.그리고수영장내락커룸바닥이수영하고나온사람들이흘린물로엉망인데직원이관리를제대로못하고있는것같습니다.
칫솔이랑 치약을 판매하네요.
사람이 너무 많아 줄 서서 체크인 하느라 체크인 시간에서 시간 소요가 많이 됨. 객실에 먼지가 많았으며 무료 와이파이가 구비되어 있지만 사용이 거의 안 됨. 침대 쪽에 콘센트가 없어서 불편했음.
조식 뷔페가 포함된 패키지를 샀는데, 뷔페를 코로나 때문에 운영하지 못하셨어요.
식사를 서빙해 주신 것 까지는 좋았는데,,,
가성비가 좋지 않았습니다.
패키지에 포함

In [18]:
repeat_normalize("아아아아아아 ㅋㅋㅋㅋㅋㅋ", num_repeats=2)

'아아 ㅋㅋ'

In [ ]:
# neg, pos division
neg = review_df[review_df["Label"] == 0]["Text"]
pos = review_df[review_df["Label"] == 1]["Text"]

def split_sentence(texts_df):
    arr = []
    for sentence in tqdm(texts_df):
        for s in kss.split_sentences(sentence):
            arr.append(s)
    return arr


neg = pd.DataFrame({"Text": split_sentence(neg)})
pos = pd.DataFrame({"Text": split_sentence(pos)})

neg["Label"] = 0
pos["Label"] = 1

# del record that have only 1 word

review_splited = pd.concat([pos, neg])
review_splited["len_text"] = [len(t.split()) for t in review_splited["Text"]]
review_splited_del_meaningless = review_splited[review_splited["len_text"] > 1]

# flushing idx

review_splited_del_meaningless.index = [i for i in range(review_splited_del_meaningless["Text"].size)]